Задача 1. Напишите функцию, принимающую на вход один длинный аудио-файл и один короткий, а также соответствующий длинному файлу TextGrid, содержащий точечный слой. Выходом функции будет новый аудио-файл, представляющий собой наложение короткого аудио на длинное в точках, отмеченных в TextGrid.

In [ ]:
!wget https://raw.githubusercontent.com/phonetics-spbu/phonetics-spbu.github.io/main/public/courses/python_2_mag/files/j39s.wav
!wget https://raw.githubusercontent.com/phonetics-spbu/phonetics-spbu.github.io/main/public/courses/python_2_mag/files/j39s_point.TextGrid
!wget https://raw.githubusercontent.com/phonetics-spbu/phonetics-spbu.github.io/main/public/courses/python_2_mag/files/mixkit-explosion-hit-1704.wav

In [22]:
!pip install tgt

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 41.6/41.6 kB 2.4 MB/s eta 0:00:00


In [23]:
import tgt

In [45]:
def create_overlayed_audio(long_audio, short_audio, textgrid):
  long_audio = AudioSegment.from_file(long_audio)
  short_audio = AudioSegment.from_file(short_audio)

  grid = tgt.io.read_textgrid(textgrid)
  point_tier = grid.get_tier_by_name("1")

  for point in point_tier:
    long_audio = long_audio.overlay(short_audio - 20, position=1000*point.time)

  return long_audio

In [46]:
audio = AudioSegment.from_file("j39s.wav")
audio

In [44]:
audio_sh = AudioSegment.from_file("mixkit-explosion-hit-1704.wav")
audio_sh

In [47]:
long_audio = "j39s.wav"
short_audio = "mixkit-explosion-hit-1704.wav"
textgrid = "j39s_point.TextGrid"

new_audio = create_overlayed_audio(long_audio, short_audio, textgrid)
new_audio

Задача 2. Напишите функцию, принимающую на вход один аудио-файл и соответствующий длинному файлу TextGrid, содержащий интервальный слой. Выходом функции будет новый аудио-файл, представляющий собой случайным образом перемешанные склеенные между собой интервалы.

In [ ]:
!wget https://raw.githubusercontent.com/phonetics-spbu/phonetics-spbu.github.io/main/public/courses/python_2_mag/files/j39s.wav
!wget https://raw.githubusercontent.com/phonetics-spbu/phonetics-spbu.github.io/main/public/courses/python_2_mag/files/j39s.TextGrid

In [48]:
import random

In [75]:
def shuffle_audio_segments(audio_fn, textgrid):
  audio = AudioSegment.from_file(audio_fn)

  grid = tgt.io.read_textgrid(textgrid)
  # print(grid.get_tier_names())
  interval_tier = grid.get_tier_by_name("2")
  # print(len(interval_tier))

  audio_segments = []

  for i in range(len(interval_tier)):
    start_time = int(interval_tier[i].start_time * 1000)
    end_time = int(interval_tier[i].end_time * 1000)
    new_segment = audio[start_time : end_time]
    audio_segments.append(new_segment)

  random.shuffle(audio_segments)

  shuffled_segments_united = AudioSegment.empty()

  for i in range(len(audio_segments)):
    shuffled_segments_united = shuffled_segments_united + audio_segments[i]

  shuffled_segments_united.export("shuffled_segments_united.wav", format="wav")

  return shuffled_segments_united

In [81]:
audio_fn = "j39s.wav"
textgrid = "j39s.TextGrid"

new_audio = shuffle_audio_segments(audio_fn, textgrid)
new_audio

Задача 3. Наложите поверх аудио с речью музыку, в паузах музыка должна становиться громче с плавным нарастанием. Даны: аудио с речью + текстгрид с разметкой пауз, аудио с музыкой.

In [91]:
!wget https://raw.githubusercontent.com/annashell/python_mag/refs/heads/main/txt_files/av18s.wav
!wget https://raw.githubusercontent.com/annashell/python_mag/refs/heads/main/txt_files/av18s.TextGrid
!wget https://raw.githubusercontent.com/phonetics-spbu/phonetics-spbu.github.io/main/public/courses/python_2_mag/files/mixkit-synth-suspense-music-681.wav

--2025-10-16 10:39:31--  https://raw.githubusercontent.com/annashell/python_mag/refs/heads/main/txt_files/av18s.wav
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.110.133, 185.199.111.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 578012 (564K) [audio/wav]
Saving to: ‘av18s.wav.2’

av18s.wav.2         100%[===================>] 564.46K  --.-KB/s    in 0.006s  

2025-10-16 10:39:31 (86.4 MB/s) - ‘av18s.wav.2’ saved [578012/578012]

--2025-10-16 10:39:31--  https://raw.githubusercontent.com/annashell/python_mag/refs/heads/main/txt_files/av18s.TextGrid
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.110.133, 185.199.111.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length:

In [98]:
def overlay_music_with_pauses(audio_fn, textgrid, music):
  audio = AudioSegment.from_file(audio_fn)
  music = AudioSegment.from_file(music) - 20

  grid = tgt.io.read_textgrid(textgrid)
  # print(grid.get_tier_names())
  interval_tier = grid.get_tier_by_name("acoustic")

  audio_segments = []

  for i in range(len(interval_tier)):
    start_time = int(interval_tier[i].start_time * 1000)
    end_time = int(interval_tier[i].end_time * 1000)
    new_segment = music[start_time : end_time]
    if interval_tier[i].text != "pause":
      audio_segments.append(new_segment)
    else:
      new_segment = new_segment.fade_in(200).fade_out(300)
      audio_segments.append(new_segment + 20)

  segments_united = AudioSegment.empty()

  for i in range(len(audio_segments)):
    segments_united = segments_united + audio_segments[i]

  res_audio = audio.overlay(segments_united)
  return res_audio

In [93]:
audio = AudioSegment.from_file("mixkit-synth-suspense-music-681.wav")
audio

In [99]:
audio_fn = "av18s.wav"
textgrid = "av18s.TextGrid"
music = "mixkit-synth-suspense-music-681.wav"

new_audio = overlay_music_with_pauses(audio_fn, textgrid, music)
new_audio

Задача 4. Вам дано короткое аудио. Необходимо написать функцию, возвращающую "эхо": периодическое повторение звука с постепенным затуханием громкости.

In [9]:
!wget https://raw.githubusercontent.com/phonetics-spbu/phonetics-spbu.github.io/main/public/courses/python_2_mag/files/j27s.wav

--2025-10-16 09:45:39--  https://raw.githubusercontent.com/phonetics-spbu/phonetics-spbu.github.io/main/public/courses/python_2_mag/files/j27s.wav
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 89234 (87K) [audio/wav]
Saving to: ‘j27s.wav.1’

j27s.wav.1          100%[===================>]  87.14K  --.-KB/s    in 0.002s  

2025-10-16 09:45:39 (37.4 MB/s) - ‘j27s.wav.1’ saved [89234/89234]



In [7]:
from pydub import AudioSegment

/usr/local/lib/python3.12/dist-packages/pydub/utils.py:300: SyntaxWarning: invalid escape sequence '\('
  m = re.match('([su]([0-9]{1,2})p?) \(([0-9]{1,2}) bit\)$', token)
/usr/local/lib/python3.12/dist-packages/pydub/utils.py:301: SyntaxWarning: invalid escape sequence '\('
  m2 = re.match('([su]([0-9]{1,2})p?)( \(default\))?$', token)
/usr/local/lib/python3.12/dist-packages/pydub/utils.py:310: SyntaxWarning: invalid escape sequence '\('
  elif re.match('(flt)p?( \(default\))?$', token):
/usr/local/lib/python3.12/dist-packages/pydub/utils.py:314: SyntaxWarning: invalid escape sequence '\('
  elif re.match('(dbl)p?( \(default\))?$', token):


In [15]:
def create_echo(filename, n, db_decrease):
  audio = AudioSegment.from_file(filename)
  audio_res = audio
  for i in range(n):
    audio_res = audio_res + AudioSegment.silent(duration=500)
    audio_res = audio_res + (audio - db_decrease * (i + 1))
  return audio_res

In [16]:
new_audio = create_echo("j27s.wav", 5, 10)

In [13]:
audio = AudioSegment.from_file("j27s.wav")
audio

In [17]:
new_audio